## Homework

In [126]:
#!wget --no-check-certificate 'https://docs.google.com/uc?export=download&id=1OKFSv2GpuUFDphO0r8LdM7bl6MAWwBfX' -O data.csv

В этой домашней работе вы будете предсказывать стоимость домов по их характеристикам.

Метрика качества: `RMSE`

Оценивание:
* Baseline - 2 балла
* Feature Engineering - 2 балла
* Model Selection - 3 балла
* Ensemble v.1 - 3 балла
* (*) Ensemble v.2 - дополнительно, 2 балла

### Описание датасета

Короткое описание данных:
```
price: sale price (this is the target variable)
id: transaction id
timestamp: date of transaction
full_sq: total area in square meters, including loggias, balconies and other non-residential areas
life_sq: living area in square meters, excluding loggias, balconies and other non-residential areas
floor: for apartments, floor of the building
max_floor: number of floors in the building
material: wall material
build_year: year built
num_room: number of living rooms
kitch_sq: kitchen area
state: apartment condition
product_type: owner-occupier purchase or investment
sub_area: name of the district

The dataset also includes a collection of features about each property's surrounding neighbourhood, and some features that are constant across each sub area (known as a Raion). Most of the feature names are self explanatory, with the following notes. See below for a complete list.

full_all: subarea population
male_f, female_f: subarea population by gender
young_*: population younger than working age
work_*: working-age population
ekder_*: retirement-age population
n_m_{all|male|female}: population between n and m years old
build_count_*: buildings in the subarea by construction type or year
x_count_500: the number of x within 500m of the property
x_part_500: the share of x within 500m of the property
_sqm_: square meters
cafe_count_d_price_p: number of cafes within d meters of the property that have an average bill under p RUB
trc_: shopping malls
prom_: industrial zones
green_: green zones
metro_: subway
_avto_: distances by car
mkad_: Moscow Circle Auto Road
ttk_: Third Transport Ring
sadovoe_: Garden Ring
bulvar_ring_: Boulevard Ring
kremlin_: City center
zd_vokzaly_: Train station
oil_chemistry_: Dirty industry
ts_: Power plant
```

### Setup

In [127]:
import pandas as pd
import numpy as np
from sklearn.datasets import make_blobs, make_circles, make_classification, load_iris, load_digits
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn import tree, metrics, model_selection
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
from collections import Counter

In [128]:
df = pd.read_csv("data.csv", parse_dates=["timestamp"])

Разделите имеющиеся у вас данные на обучающую и тестовую выборки. В качестве обучающей выборки возьмите первые 80% данных, последние 20% - тестовая выборка.

In [129]:
df = df.dropna()

In [130]:
X = df.drop('price', axis=1)
y = df['price']

In [131]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

Возможно в ваших моделях вам придется указывать, какие колонки являются категориальными (например, в бустингах). Для упрощения предлагается разделить колонки по следующему принципу:
```
drop_columns = [
    'id',           # May leak information
    'timestamp',    # May leak information
]
cat_columns = [
    'product_type',              #
    'material',                  # Material of the wall
    'state',                     # Satisfaction level
    'sub_area',                  # District name
    'culture_objects_top_25',    #
    'thermal_power_plant_raion', #
    'incineration_raion',        #
    'oil_chemistry_raion',       #
    'radiation_raion',           #
    'railroad_terminal_raion',   #
    'big_market_raion',          #
    'nuclear_reactor_raion',     #
    'detention_facility_raion',  #
    'ID_metro',                  #
    'ID_railroad_station_walk',  #
    'ID_railroad_station_avto',  #
    'water_1line',               #
    'ID_big_road1',              #
    'big_road1_1line',           #
    'ID_big_road2',              #
    'railroad_1line',            #
    'ID_railroad_terminal',      #
    'ID_bus_terminal',           #
    'ecology',                   #
]
num_columns = list(set(df.columns).difference(set(cat_columns + drop_columns)))
```

In [132]:
drop_columns = [
    'id',           # May leak information
    'timestamp',    # May leak information
]

cat_columns = [
    'product_type',              #
    'material',                  # Material of the wall
    'state',                     # Satisfaction level
    'sub_area',                  # District name
    'culture_objects_top_25',    #
    'thermal_power_plant_raion', #
    'incineration_raion',        #
    'oil_chemistry_raion',       #
    'radiation_raion',           #
    'railroad_terminal_raion',   #
    'big_market_raion',          #
    'nuclear_reactor_raion',     #
    'detention_facility_raion',  #
    'ID_metro',                  #
    'ID_railroad_station_walk',  #
    'ID_railroad_station_avto',  #
    'water_1line',               #
    'ID_big_road1',              #
    'big_road1_1line',           #
    'ID_big_road2',              #
    'railroad_1line',            #
    'ID_railroad_terminal',      #
    'ID_bus_terminal',           #
    'ecology',                   #
]

target_column = ['price']

num_columns = list(set(df.columns).difference(set(cat_columns + drop_columns + target_column)))

### Baseline (2 балла)

В качестве Baseline обучите `DecisionTreeRegressor` из `sklearn`.

In [133]:
N = 50

In [134]:
score0 = np.zeros(N)

for n in range(N):
    baseline_model = DecisionTreeRegressor().fit(X_train[num_columns], y_train)
    score0[n] = metrics.mean_squared_error(y_test, baseline_model.predict(X_test[num_columns]))

Проверьте качество на отложенной выборке.

In [135]:
score0.mean()

24545767189790.215

### Feature Engineering (2 балла)

Часто улучшить модель можно с помощью аккуратного Feature Engineering.

Добавим в модель дополнительные признаки:
* "Как часто в этот год и этот месяц появлились объявления"
* "Как часто в этот год и эту неделю появлялись объявления"

In [136]:
X = df.drop('price', axis=1)
y = df['price']

In [137]:
month_year = (df.timestamp.dt.month + df.timestamp.dt.year * 100)
month_year_cnt_map = month_year.value_counts().to_dict()
X["month_year_cnt"] = month_year.map(month_year_cnt_map)

week_year = (df.timestamp.dt.weekofyear + df.timestamp.dt.year * 100)
week_year_cnt_map = week_year.value_counts().to_dict()
X["week_year_cnt"] = week_year.map(week_year_cnt_map)

/var/folders/9j/cllsf0815jl9bm0yjv_8cm400000gn/T/ipykernel_17222/3259660219.py:5: FutureWarning: Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.
  week_year = (df.timestamp.dt.weekofyear + df.timestamp.dt.year * 100)


Добавьте следюущие дополнительные признаки:
* Месяц (из колонки `timestamp`)
* День недели (из колонки `timestamp`)
* Отношение "этаж / максимальный этаж в здании" (колонки `floor` и `max_floor`)
* Отношение "площадь кухни / площадь квартиры" (колонки `kitchen_sq` и `full_sq`)

По желанию можно добавить и другие признаки.

In [138]:
X['month'] = X.timestamp.dt.month
X['week_day'] = X.timestamp.dt.weekday

X['floor_max_floor'] = X['floor'] / X['max_floor']
X.loc[X['floor_max_floor'] == np.inf, 'floor_max_floor'] = np.NaN
X['floor_max_floor'] = X['floor_max_floor'].fillna(X['floor_max_floor'][X['floor_max_floor'].notna()].mean())

X['kitch_full'] = X['kitch_sq'] / X['full_sq']
X.loc[X['kitch_full'] == np.inf, 'kitch_full'] = np.NaN
X['kitch_full'] = X['kitch_full'].fillna(X['kitch_full'][X['kitch_full'].notna()].mean())

In [139]:
X['culture_objects_top_25_int'] = (X['culture_objects_top_25'] == 'yes')
X['thermal_power_plant_int'] = (X['thermal_power_plant_raion'] == 'yes')
X['incineration_raion_int'] = (X['incineration_raion'] == 'yes')
X['oil_chemistry_raion_int'] = (X['oil_chemistry_raion'] == 'yes')
X['radiation_raion_int'] = (X['radiation_raion'] == 'yes')
X['railroad_terminal_raion_int'] = (X['railroad_terminal_raion'] == 'yes')
X['big_market_raion_int'] = (X['big_market_raion'] == 'yes')
X['nuclear_reactor_raion_int'] = (X['nuclear_reactor_raion'] == 'yes')
X['detention_facility_raion_int'] = (X['detention_facility_raion'] == 'yes')
X['product_type_int'] = (X['product_type'] == 'yes')

In [140]:
try:
    X = X.drop(['kitch_sq'], axis=1)
except KeyError:
    print('already deleted')

Разделите выборку на обучающую и тестовую еще раз (потому что дополнительные признаки созданы для исходной выборки).

In [141]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [142]:
num_columns = list(set(X.columns).difference(set(cat_columns + drop_columns + target_column)))

In [143]:
score1 = np.zeros(N)

for n in range(N):
    model1 = DecisionTreeRegressor().fit(X_train[num_columns], y_train)
    score1[n] = metrics.mean_squared_error(y_test, model1.predict(X_test[num_columns]))

In [144]:
print(score1.mean() / score0.mean())

0.962963401807086


### Model Selection (3 балла)

Посмотрите, какого качества можно добиться если использовать разные модели:
* `DecisionTreeRegressor` из `sklearn`
* `RandomForestRegressor` из `sklearn`
* `CatBoostRegressor`

Также вы можете попробовать линейные модели, другие бустинги (`LigthGBM` и `XGBoost`).

Почти все библиотеки поддерживают удобный способ подбора гиперпараметров: посмотрите как это делать в [sklearn](https://scikit-learn.org/stable/modules/generated/sklearn.model_selection.GridSearchCV.html) или в [catboost](https://catboost.ai/docs/concepts/python-reference_catboostregressor_grid_search.html).

Проверяйте качество каждой модели на тестовой выборке и выберите наилучшую.

In [145]:
from sklearn.model_selection import GridSearchCV

params = {'min_samples_split': range(2, 10), 'max_features': [None, 5, 20, 40, 50], 'max_leaf_nodes': [None, 10, 20, 30]}

search = GridSearchCV(estimator=DecisionTreeRegressor(), param_grid=params, scoring='neg_root_mean_squared_error', cv=5)

search.fit(X_train[num_columns], y_train)

DecisionTreeBest = search.best_params_

y_pred = search.predict(X_test[num_columns])

print(metrics.mean_squared_error(y_test, y_pred) / score0.mean())

0.8265162503067081


In [146]:
from sklearn.model_selection import GridSearchCV

params = {'n_estimators': np.arange(100, 500, 100), 'max_leaf_nodes': [None, 10, 20]}

search = GridSearchCV(estimator=RandomForestRegressor(), param_grid=params, scoring='neg_root_mean_squared_error', cv=5)

search.fit(X_train[num_columns], y_train)

RandomForestBest = search.best_params_

y_pred = search.predict(X_test[num_columns])

print(metrics.mean_squared_error(y_test, y_pred) / score0.mean())

0.566789759677176


In [187]:
from catboost import CatBoostRegressor

params = {'iterations': [100, 150, 200], 'learning_rate': [0.03, 0.1], 'depth': [2, 4, 6, 8], 'l2_leaf_reg': [0.2, 0.5, 1, 3]}

search = GridSearchCV(estimator=CatBoostRegressor(), param_grid=params, scoring='neg_root_mean_squared_error', cv=5)

search.fit(X_train[num_columns], y_train)

CatBoostBest = search.best_params_

y_pred = search.predict(X_test[num_columns])

print(metrics.mean_squared_error(y_test, y_pred) / score0.mean())

0:	learn: 5906358.9133851	total: 1.68ms	remaining: 166ms
1:	learn: 5901036.8770587	total: 3.4ms	remaining: 167ms
2:	learn: 5895670.2111070	total: 5.41ms	remaining: 175ms
3:	learn: 5890568.5663662	total: 7.18ms	remaining: 172ms
4:	learn: 5889052.1437271	total: 8.75ms	remaining: 166ms
5:	learn: 5886662.4109172	total: 10.6ms	remaining: 167ms
6:	learn: 5882264.9434687	total: 13.3ms	remaining: 177ms
7:	learn: 5881434.1875789	total: 14.5ms	remaining: 167ms
8:	learn: 5878721.0931581	total: 16ms	remaining: 162ms
9:	learn: 5871149.8225255	total: 17.4ms	remaining: 156ms
10:	learn: 5867805.4545783	total: 18.7ms	remaining: 151ms
11:	learn: 5863835.2394929	total: 19.9ms	remaining: 146ms
12:	learn: 5862270.3973252	total: 20.9ms	remaining: 140ms
13:	learn: 5860071.6768447	total: 21.9ms	remaining: 135ms
14:	learn: 5859419.9281996	total: 23.1ms	remaining: 131ms
15:	learn: 5858064.4791471	total: 24.5ms	remaining: 129ms
16:	learn: 5855843.9303198	total: 25.7ms	remaining: 125ms
17:	learn: 5851577.8533993	

In [149]:
from sklearn.model_selection import GridSearchCV

from sklearn.linear_model import Lasso

params = {'max_iter': np.arange(200, 2000, 200), 'alpha': np.arange(0.1, 1.1, 0.1)}

search = GridSearchCV(estimator=Lasso(), param_grid=params, scoring='neg_root_mean_squared_error', cv=5)

search.fit(X_train[num_columns], y_train)

Lasso_best = search.best_params_

y_pred = search.predict(X_test[num_columns])

print(metrics.mean_squared_error(y_test, y_pred) / score0.mean())

/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.656e+16, tolerance: 8.118e+12
  model = cd_fast.enet_coordinate_descent(
/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.565e+16, tolerance: 7.757e+12
  model = cd_fast.enet_coordinate_descent(
/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.818e+16, tolerance: 

0.6574036192332686


/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 2.165e+16, tolerance: 1.077e+13
  model = cd_fast.enet_coordinate_descent(


### Ensemble v.1 (3 балла)

Ансамбли иногда оказываются лучше чем одна большая модель.

В колонке `product_type` содержится информация о том, каким является объявление: `Investment` (продажа квартиры как инвестиции) или `OwnerOccupier` (продажа квартиры для жилья). Логично предположить, что если сделать по модели на каждый из этих типов, то качество будет выше.

Обучите свои лучшие модели на отдельно на `Investment` и `OwnerOccupier` (т.е. у вас будет `model_invest`, обученная на `(invest_train_X, invest_train_Y)` и `model_owner`, обученная на `(owner_train_X, owner_train_Y)`) и проверьте качество на отложенной выборке (т.е. на исходном `test_split`).

In [156]:
X_test_i = X_test[X_test['product_type'] == 'Investment']
X_train_i = X_train[X_train['product_type'] == 'Investment']
y_test_i = y_test[X_test['product_type'] == 'Investment']
y_train_i = y_train[X_train['product_type'] == 'Investment']

X_test_o = X_test[X_test['product_type'] == 'OwnerOccupier']
X_train_o = X_train[X_train['product_type'] == 'OwnerOccupier']
y_test_o = y_test[X_test['product_type'] == 'OwnerOccupier']
y_train_o = y_train[X_train['product_type'] == 'OwnerOccupier']

In [173]:
y_pred_i = DecisionTreeRegressor(max_features=DecisionTreeBest['max_features'],
                max_leaf_nodes=DecisionTreeBest['max_leaf_nodes'],
                min_samples_split=DecisionTreeBest['min_samples_split']).fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_o = DecisionTreeRegressor(max_features=DecisionTreeBest['max_features'],
                max_leaf_nodes=DecisionTreeBest['max_leaf_nodes'],
                min_samples_split=DecisionTreeBest['min_samples_split']).fit(X_train_o[num_columns], y_train_o).predict(X_test_o[num_columns])

y_pred = np.hstack((y_pred_i, y_pred_o)).flatten()
y_test = np.hstack((y_test_i, y_test_o)).flatten()

print(metrics.mean_squared_error(y_pred, y_test) / score0.mean())

0.784878161436677


In [177]:
y_pred_i = RandomForestRegressor(n_estimators=RandomForestBest['n_estimators'],
                max_leaf_nodes=RandomForestBest['max_leaf_nodes']).fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_o = RandomForestRegressor(n_estimators=RandomForestBest['n_estimators'],
                max_leaf_nodes=RandomForestBest['max_leaf_nodes']).fit(X_train_o[num_columns], y_train_o).predict(X_test_o[num_columns])

y_pred = np.hstack((y_pred_i, y_pred_o)).flatten()
y_test = np.hstack((y_test_i, y_test_o)).flatten()

print(metrics.mean_squared_error(y_pred, y_test) / score0.mean())

0.5961408737848524


In [183]:
y_pred_i = Lasso(alpha=Lasso_best['alpha'],
                max_iter=Lasso_best['max_iter']).fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_o = Lasso(alpha=Lasso_best['alpha'],
                max_iter=Lasso_best['max_iter']).fit(X_train_o[num_columns], y_train_o).predict(X_test_o[num_columns])

y_pred = np.hstack((y_pred_i, y_pred_o)).flatten()
y_test = np.hstack((y_test_i, y_test_o)).flatten()

print(metrics.mean_squared_error(y_pred, y_test) / score0.mean())

0.8009271962603143


/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 1.573e+16, tolerance: 9.671e+12
  model = cd_fast.enet_coordinate_descent(
/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_coordinate_descent.py:647: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 5.426e+14, tolerance: 1.008e+12
  model = cd_fast.enet_coordinate_descent(


In [188]:
CatBoostBest

{'depth': 4, 'iterations': 100, 'l2_leaf_reg': 3, 'learning_rate': 0.03}

In [189]:
y_pred_i = CatBoostRegressor(depth=CatBoostBest['depth'], iterations=CatBoostBest['iterations'], l2_leaf_reg=CatBoostBest['l2_leaf_reg'],
                learning_rate=CatBoostBest['learning_rate']).fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_o = CatBoostRegressor(depth=CatBoostBest['depth'], iterations=CatBoostBest['iterations'], l2_leaf_reg=CatBoostBest['l2_leaf_reg'],
                learning_rate=CatBoostBest['learning_rate']).fit(X_train_o[num_columns], y_train_o).predict(X_test_o[num_columns])

y_pred = np.hstack((y_pred_i, y_pred_o)).flatten()
y_test = np.hstack((y_test_i, y_test_o)).flatten()

print(metrics.mean_squared_error(y_pred, y_test) / score0.mean())

0:	learn: 5800242.7861628	total: 3.5ms	remaining: 346ms
1:	learn: 5721487.9200219	total: 6.78ms	remaining: 332ms
2:	learn: 5644004.9095478	total: 10.1ms	remaining: 327ms
3:	learn: 5564550.3786914	total: 13.5ms	remaining: 325ms
4:	learn: 5495128.5938210	total: 16.4ms	remaining: 311ms
5:	learn: 5421766.6037435	total: 20.1ms	remaining: 314ms
6:	learn: 5355441.6435522	total: 22.9ms	remaining: 304ms
7:	learn: 5288925.0808113	total: 25.9ms	remaining: 298ms
8:	learn: 5224433.0407825	total: 29.1ms	remaining: 295ms
9:	learn: 5166287.3682042	total: 31.7ms	remaining: 285ms
10:	learn: 5108287.4516365	total: 34.9ms	remaining: 283ms
11:	learn: 5045992.7160764	total: 37.6ms	remaining: 276ms
12:	learn: 4990833.5065768	total: 40.4ms	remaining: 271ms
13:	learn: 4937892.3360743	total: 43.1ms	remaining: 265ms
14:	learn: 4893749.6347679	total: 45.4ms	remaining: 257ms
15:	learn: 4845049.8880689	total: 47.7ms	remaining: 250ms
16:	learn: 4797479.6969988	total: 50.3ms	remaining: 246ms
17:	learn: 4751747.346528

### (*) Ensemble v.2 (дополнительно, 2 балла)

Попробуйте сделать для `Investment` более сложную модель: обучите `CatBoostRegressor` и `HuberRegressor` из `sklearn`, а затем сложите их предсказания с весами `w_1` и `w_2` (выберите веса сами; сумма весов равняется 1).

In [190]:
from sklearn.linear_model import HuberRegressor

y_pred_i_1 = CatBoostRegressor(depth=CatBoostBest['depth'], iterations=CatBoostBest['iterations'], l2_leaf_reg=CatBoostBest['l2_leaf_reg'],
                learning_rate=CatBoostBest['learning_rate']).fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_i_2 = HuberRegressor().fit(X_train_i[num_columns], y_train_i).predict(X_test_i[num_columns])

y_pred_o = RandomForestRegressor(n_estimators=RandomForestBest['n_estimators'],
                max_leaf_nodes=RandomForestBest['max_leaf_nodes']).fit(X_train_o[num_columns], y_train_o).predict(X_test_o[num_columns])

0:	learn: 5800242.7861628	total: 2.31ms	remaining: 228ms
1:	learn: 5721487.9200219	total: 6.79ms	remaining: 333ms
2:	learn: 5644004.9095478	total: 9.74ms	remaining: 315ms
3:	learn: 5564550.3786914	total: 12.6ms	remaining: 302ms
4:	learn: 5495128.5938210	total: 16.5ms	remaining: 313ms
5:	learn: 5421766.6037435	total: 19.2ms	remaining: 301ms
6:	learn: 5355441.6435522	total: 22.4ms	remaining: 298ms
7:	learn: 5288925.0808113	total: 24.8ms	remaining: 285ms
8:	learn: 5224433.0407825	total: 27.4ms	remaining: 277ms
9:	learn: 5166287.3682042	total: 31ms	remaining: 279ms
10:	learn: 5108287.4516365	total: 33.8ms	remaining: 273ms
11:	learn: 5045992.7160764	total: 36.7ms	remaining: 269ms
12:	learn: 4990833.5065768	total: 40.4ms	remaining: 270ms
13:	learn: 4937892.3360743	total: 43.1ms	remaining: 264ms
14:	learn: 4893749.6347679	total: 46.7ms	remaining: 264ms
15:	learn: 4845049.8880689	total: 49.7ms	remaining: 261ms
16:	learn: 4797479.6969988	total: 52.3ms	remaining: 256ms
17:	learn: 4751747.3465289

/opt/homebrew/lib/python3.9/site-packages/sklearn/linear_model/_huber.py:332: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  self.n_iter_ = _check_optimize_result("lbfgs", opt_res, self.max_iter)


In [199]:
y_pred_i = 1.2 * y_pred_i_1 - 0.2 * y_pred_i_2

y_pred = np.hstack((y_pred_i, y_pred_o)).flatten()
y_test = np.hstack((y_test_i, y_test_o)).flatten()

print(metrics.mean_squared_error(y_pred, y_test) / score0.mean())

0.6009195311378481
